In [1]:
import gymnasium as gym
from pogema import GridConfig
from stable_baselines3 import DQN, A2C
from stable_baselines3.common.evaluation import evaluate_policy

%load_ext autoreload
%autoreload 2
%matplotlib inline

grid_config = GridConfig(
    size=8,
    density=0.3,
    num_agents=1,
    max_episode_steps=128,
    obs_radius=3
)

env = gym.make("Pogema-v0",grid_config=grid_config)

a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1
)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:29: UserWarning: WARN: It seems a Box observation space is an image but the `dtype` is not `np.uint8`, actual type: float32. If the Box observation space is not an image, we recommend flattening the observation to have only a 1D vector.
  logger.warn(
/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/gymnasium/utils/passive_env_checker.py:34: UserWarning: WARN: It seems a Box observation space is an image but the lower and upper bounds are not [0, 255]. Actual lower bound: -1.0, upper bound: 1.0. Generally, CNN policies assume observations are within that range, so you may encounter an issue if the observation values are not.
  logger.warn(


#### Optuna Integration

In [2]:
""" Optuna example that optimizes the hyperparameters of
a reinforcement learning agent using A2C implementation from Stable-Baselines3
on a Gymnasium environment.

This is a simplified version of what can be found in https://github.com/DLR-RM/rl-baselines3-zoo.

You can run this example as follows:
    $ python sb3_simple.py

"""
from typing import Any
from typing import Dict

import gymnasium
import optuna
from optuna.pruners import MedianPruner
from optuna.samplers import TPESampler
from stable_baselines3 import A2C
from stable_baselines3.common.callbacks import EvalCallback
from stable_baselines3.common.monitor import Monitor
import torch
import torch.nn as nn


N_TRIALS = 100
N_STARTUP_TRIALS = 5
N_EVALUATIONS = 2
N_TIMESTEPS = int(1.0e4)
EVAL_FREQ = int(N_TIMESTEPS / N_EVALUATIONS)
N_EVAL_EPISODES = 3


DEFAULT_HYPERPARAMS = {
    "policy": "MlpPolicy",
    "verbose": 1,
    "env": env
}

def sample_a2c_params(trial: optuna.Trial) -> Dict[str, Any]:
    """Sampler for A2C hyperparameters."""
    gamma = 1.0 - trial.suggest_float("gamma", 0.0001, 0.1, log=True)
    learning_rate = trial.suggest_float("lr", 1e-5, 1, log=True)

    trial.set_user_attr("gamma", gamma)

    return {
        "gamma": gamma,
        "learning_rate": learning_rate,
    }


class TrialEvalCallback(EvalCallback):
    """Callback used for evaluating and reporting a trial."""

    def __init__(
        self,
        eval_env: gymnasium.Env,
        trial: optuna.Trial,
        n_eval_episodes: int = 5,
        eval_freq: int = 10000,
        deterministic: bool = True,
        verbose: int = 0,
    ):
        super().__init__(
            eval_env=eval_env,
            n_eval_episodes=n_eval_episodes,
            eval_freq=eval_freq,
            deterministic=deterministic,
            verbose=verbose,
        )
        self.trial = trial
        self.eval_idx = 0
        self.is_pruned = False

    def _on_step(self) -> bool:
        if self.eval_freq > 0 and self.n_calls % self.eval_freq == 0:
            super()._on_step()
            self.eval_idx += 1
            self.trial.report(self.last_mean_reward, self.eval_idx)
            # Prune trial if need.
            if self.trial.should_prune():
                self.is_pruned = True
                return False
        return True


def objective(trial: optuna.Trial) -> float:
    kwargs = DEFAULT_HYPERPARAMS.copy()
    # Sample hyperparameters.
    kwargs.update(sample_a2c_params(trial))
    # Create the RL model.
    model = A2C(**kwargs)
    # Create env used for evaluation.
    eval_env = Monitor(env)
    # Create the callback that will periodically evaluate and report the performance.
    eval_callback = TrialEvalCallback(
        eval_env, trial, n_eval_episodes=N_EVAL_EPISODES, eval_freq=EVAL_FREQ, deterministic=True
    )

    nan_encountered = False
    try:
        model.learn(N_TIMESTEPS, callback=eval_callback)
    except AssertionError as e:
        # Sometimes, random hyperparams can generate NaN.
        print(e)
        nan_encountered = True
    finally:
        # Free memory.
        model.env.close()
        eval_env.close()

    # Tell the optimizer that the trial failed.
    if nan_encountered:
        return float("nan")

    if eval_callback.is_pruned:
        raise optuna.exceptions.TrialPruned()

    return eval_callback.last_mean_reward


if __name__ == "__main__":
    # Set pytorch num threads to 1 for faster training.
    torch.set_num_threads(1)

    sampler = TPESampler(n_startup_trials=N_STARTUP_TRIALS)
    # Do not prune before 1/3 of the max budget is used.
    pruner = MedianPruner(n_startup_trials=N_STARTUP_TRIALS, n_warmup_steps=N_EVALUATIONS // 3)

    study = optuna.create_study(sampler=sampler, pruner=pruner, direction="maximize")
    try:
        study.optimize(objective, n_trials=N_TRIALS, n_jobs=4, timeout=600)
    except KeyboardInterrupt:
        pass

    print("Number of finished trials: ", len(study.trials))

    print("Best trial:")
    trial = study.best_trial

    print("  Value: ", trial.value)

    print("  Params: ")
    for key, value in trial.params.items():
        print("    {}: {}".format(key, value))

    print("  User attrs:")
    for key, value in trial.user_attrs.items():
        print("    {}: {}".format(key, value))


/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
[I 2023-11-10 17:20:44,841] A new study created in memory with name: no-name-524e7d75-8d7a-4d81-bcb0-14ed89b8a1da
[W ParallelNative.cpp:230] Warning: Cannot set number of intraop threads after parallel work has started or after set_num_threads call when using native parallel backend (function set_num_threads)


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 93.8      |
|    ep_rew_mean        | 0.2       |
| time/                 |           |
|    fps                | 209       |
|    iterations         | 100       |
|    time_elapsed       | 2         |
|    total_timesteps    | 500       |
| train/                |           |
|    entropy_loss       | -3.52e-40 |
|    explained_variance | -1.51e+11 |
|    learning_rate      | 0.447     |
|    n_updates          | 99        |
|    policy_loss        | -0        |
|    value_loss         | 22.9      |
----------------

[I 2023-11-10 17:21:44,158] Trial 0 finished with value: 0.0 and parameters: {'gamma': 0.00018636767042011222, 'lr': 0.4471282662030949}. Best is trial 0 with value: 0.0.


Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
------------------------------------
| eval/                 |          |
|    mean_ep_length     | 83       |
|    mean_reward        | 0.333    |
| time/                 |          |
|    total_timesteps    | 10000    |
| train/                |          |
|    entropy_loss       | -1.59    |
|    explained_variance | -216     |
|    learning_rate      | 0.000193 |
|    n_updates          | 1999     |
|    policy_loss        | -0.0268  |
|    value_loss         | 0.0129   |
------------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 72.2     |
|    ep_rew_mean     | 0.48     |
| time/              |          |
|    fps             | 166      |
|    iterations      | 2000     |
|    time_elapsed    | 60       |
|    total_timesteps | 10000    |
---------------------------------


[I 2023-11-10 17:21:45,081] Trial 2 finished with value: 0.3333333333333333 and parameters: {'gamma': 0.09993907433325912, 'lr': 0.00019329599456242825}. Best is trial 2 with value: 0.3333333333333333.


...

------------------------------------
| eval/                 |          |
|    mean_ep_length     | 130      |
|    mean_reward        | 0        |
| time/                 |          |
|    total_timesteps    | 10000    |
| train/                |          |
|    entropy_loss       | -1.61    |
|    explained_variance | -404     |
|    learning_rate      | 2.05e-05 |
|    n_updates          | 1999     |
|    policy_loss        | -0.244   |
|    value_loss         | 0.0861   |
------------------------------------
---------------------------------
| rollout/           |          |
|    ep_len_mean     | 75.1     |
|    ep_rew_mean     | 0.5      |
| time/              |          |
|    fps             | 232      |
|    iterations      | 2000     |
|    time_elapsed    | 42       |
|    total_timesteps | 10000    |
---------------------------------


[I 2023-11-10 17:30:23,593] Trial 44 finished with value: 0.0 and parameters: {'gamma': 0.05320464176079523, 'lr': 2.0526861812999135e-05}. Best is trial 34 with value: 1.0.


------------------------------------
| rollout/              |          |
|    ep_len_mean        | 94.6     |
|    ep_rew_mean        | 0.368    |
| time/                 |          |
|    fps                | 239      |
|    iterations         | 1100     |
|    time_elapsed       | 23       |
|    total_timesteps    | 5500     |
| train/                |          |
|    entropy_loss       | -1.61    |
|    explained_variance | -182     |
|    learning_rate      | 4.79e-05 |
|    n_updates          | 1099     |
|    policy_loss        | 0.0961   |
|    value_loss         | 0.0374   |
------------------------------------
------------------------------------
| rollout/              |          |
|    ep_len_mean        | 96.6     |
|    ep_rew_mean        | 0.361    |
| time/                 |          |
|    fps                | 258      |
|    iterations         | 1200     |
|    time_elapsed       | 23       |
|    total_timesteps    | 6000     |
| train/                |          |
|

[I 2023-11-10 17:30:25,474] Trial 45 finished with value: 0.0 and parameters: {'gamma': 0.05326799764287967, 'lr': 4.789654290415112e-05}. Best is trial 34 with value: 1.0.


Number of finished trials:  47
Best trial:
  Value:  1.0
  Params: 
    gamma: 0.03288164634677655
    lr: 6.949018099784743e-05
  User attrs:
    gamma: 0.9671183536532234


### Train agent with best hyper parameters

In [7]:
a2c_model = A2C(
    "MlpPolicy",
    env,
    verbose=1,
    gamma=1-0.0033700061384865873,
    learning_rate=0.08419759274683712,
)

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [8]:
# Train agent and save it
a2c_model.learn(int(1.0e4))
a2c_model.save("saved/a2c_c_mini")

-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 128       |
|    ep_rew_mean        | 0         |
| time/                 |           |
|    fps                | 2141      |
|    iterations         | 100       |
|    time_elapsed       | 0         |
|    total_timesteps    | 500       |
| train/                |           |
|    entropy_loss       | -4.39e-21 |
|    explained_variance | 0         |
|    learning_rate      | 0.0842    |
|    n_updates          | 99        |
|    policy_loss        | -0        |
|    value_loss         | 0.000294  |
-------------------------------------
-------------------------------------
| rollout/              |           |
|    ep_len_mean        | 128       |
|    ep_rew_mean        | 0         |
| time/                 |           |
|    fps                | 2226      |
|    iterations         | 200       |
|    time_elapsed       | 0         |
|    total_timesteps    | 1000      |
| train/    

#### Testing 

In [9]:
a2c_model = A2C.load("saved/a2c_c_mini")

env.reset()

mean_reward, std_reward = evaluate_policy(a2c_model, env, deterministic=True, n_eval_episodes=20)
print(f"mean_reward:{mean_reward:.2f} +/- {std_reward:.2f}")

/Users/aditya/miniconda3/envs/pogema/lib/python3.9/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


mean_reward:0.00 +/- 0.00


In [10]:
# RANDOM SEED
from IPython.display import SVG, display
from pogema.animation import AnimationMonitor, AnimationConfig

env = AnimationMonitor(env)

def evaluate_success_rate(model, env, num_episodes=1000):
    success_count = 0
    step_array = []
    for i in range(num_episodes):
        print(f'---{i}---')
        obs = env.reset()

        # Check if observation is a tuple and extract the first element if true.
        if isinstance(obs, tuple):
            obs = obs[0]
        max_step = 128
        steps_taken = 0
        done = truncated = False
        while not done and max_step > 0:
            action, _ = model.predict(obs)
            next_obs, reward, done, truncated, info = env.step(action)
            print(action,max_step,success_count,done)
            max_step -= 1
            steps_taken += 1
            # Check if next_obs is a tuple and extract the first element if true.
            if isinstance(next_obs, tuple):
                next_obs = next_obs[0]
            obs = next_obs

            # Check if agent was successful in that episode.
            if done:
                success_count += 1
                step_array.append(steps_taken)
                env.save_animation(f"render{i}.svg", AnimationConfig(egocentric_idx=0))
                break

    success_rate = success_count / num_episodes
    return success_rate, step_array

success_rate,step_array = evaluate_success_rate(a2c_model, env)
print(f"Agent Success Rate: {success_rate * 100:.2f}%")
print(f"steps to termination : {step_array}")

---0---
1 128 0 False
1 127 0 False
1 126 0 False
1 125 0 False
1 124 0 False
1 123 0 False
1 122 0 False
1 121 0 False
1 120 0 False
1 119 0 False
1 118 0 False
1 117 0 False
1 116 0 False
1 115 0 False
1 114 0 False
1 113 0 False
1 112 0 False
1 111 0 False
1 110 0 False
1 109 0 False
1 108 0 False
1 107 0 False
1 106 0 False
1 105 0 False
1 104 0 False
1 103 0 False
1 102 0 False
1 101 0 False
1 100 0 False
1 99 0 False
1 98 0 False
1 97 0 False
1 96 0 False
1 95 0 False
1 94 0 False
1 93 0 False
1 92 0 False
1 91 0 False
1 90 0 False
1 89 0 False
1 88 0 False
1 87 0 False
1 86 0 False
1 85 0 False
1 84 0 False
1 83 0 False
1 82 0 False
1 81 0 False
1 80 0 False
1 79 0 False
1 78 0 False
1 77 0 False
1 76 0 False
1 75 0 False
1 74 0 False
1 73 0 False
1 72 0 False
1 71 0 False
1 70 0 False
1 69 0 False
1 68 0 False
1 67 0 False
1 66 0 False
1 65 0 False
1 64 0 False
1 63 0 False
1 62 0 False
1 61 0 False
1 60 0 False
1 59 0 False
1 58 0 False
1 57 0 False
1 56 0 False
1 55 0 False
1